## Attempt to get Tripifier working

In [1]:
%load_ext autoreload
%autoreload 2

from typing import List, Dict
from google.transit import gtfs_realtime_pb2 as gtfs_rt
from protobuf_to_dict import protobuf_to_dict
import pandas as pd
import numpy as np
from os import listdir
from os.path import isfile, join
import re
from datetime import datetime
import sys, os

from pandas.io.json import json_normalize
from itertools import groupby

# TODO better way to import module?
sys.path.insert(0, os.path.realpath('/content/jupyter/mta-accessibility/notebooks/routing'))
import GTFS_Utils as gu

# TODO fork tripifier eventually
# Import local version of tripifier
sys.path.insert(0, os.path.abspath('/content/jupyter/gtfs-tripify/'))
import gtfs_tripify as gt
from gtfs_tripify import tripify as tp

In [32]:
%%time

file_names = gu.get_file_names('20190601', 'ace', '20190601')
feed = gtfs_rt.FeedMessage()

feed_dicts = []
for file_path in file_names:
    with open(file_path, 'rb') as file:        
        raw_str = file.read()
        feed.ParseFromString(raw_str)
        dt = tp.dictify(feed)
        feed_dicts.append(dt)    

/opt/conda/envs/py3/lib/python3.6/site-packages/ipykernel_launcher.py:8: RuntimeWarning: Unexpected end-group tag: Not all data was converted
  


In [35]:
len(feed_dicts)

3301

In [ ]:
%%time 
log_book = gt.logify(feed_dicts)

In [ ]:
len(log_book)

In [29]:


path = '201906/20190601/gtfs_ace_20190601_041956.gtfs'
path2 = '20190601/gtfs_ace_20190601_062632.gtfs'

feed = gtfs_rt.FeedMessage()
feed2 = gtfs_rt.FeedMessage()

raw_str = None
raw_str2 = None

log = None
with open(path, 'rb') as file:
    raw_str = file.read()
with open(path2, 'rb') as file:
    raw_str2 = file.read()

feed.ParseFromString(raw_str)
dt = tp.dictify(feed) 

feed.ParseFromString(raw_str2)
dt2 = tp.dictify(feed)
print(dt['header'])
print(dt2['header'])
#log = gt.logify([dt])
    
#dt1 = protobuf_to_dict(feed1)
#dt2 = protobuf_to_dict(feed2)

#gt.logify([dt1, dt2])    

{'gtfs_realtime_version': '1.0', 'timestamp': 1559377196}
{'gtfs_realtime_version': '1.0', 'timestamp': 1559384792}


In [28]:
log_book,timestamps,parse_errors = log





In [42]:
#pd.DataFrame.from_dict(log_book, index=[0])
#pd.DataFrame.from_records(log_book)

In [50]:
log_df = pd.DataFrame()
for df in log_book.values():
    log._df.concat(df)
    


AttributeError: 'tuple' object has no attribute '_df'

In [ ]:
df = log_book['024851_E..N_1559377196']
stop_df = pd.read_csv('google_transit/stops.txt')
df = df.merge(stop_df[['stop_id', 'stop_name']], on='stop_id')
df.head()

In [34]:
df = log_book['026950_A..S_1559377196']
stop_df = pd.read_csv('google_transit/stops.txt')
df = df.merge(stop_df[['stop_id', 'stop_name']], on='stop_id')
df.head()

NameError: name 'log_book' is not defined

In [ ]:
logify("20190601/", "output", False, True, True, "csv")

In [5]:
%%time
from zipfile import ZipFile
import os

messages = []    
file_names = gu.get_file_names('20190601', 'ace', '20190601')
for file_name in file_names:
    with open(file_name, 'rb') as f:
        messages.append(f.read())

# build the logbooks
first_logbook, first_logbook_timestamps, _ = gt.logify(messages[:len(messages) // 2])
second_logbook, second_logbook_timestamps, _ = gt.logify(messages[len(messages) // 2:])

# merge the logbooks
logbook = gt.ops.merge_logbooks(
    [(first_logbook, first_logbook_timestamps), (second_logbook, second_logbook_timestamps)]    
)

# save to disk
gt.ops.to_csv(logbook, 'logbook.csv')

/content/jupyter/gtfs-tripify/gtfs_tripify/ops.py:177: UserWarning: The trip with the ID 038325_E..N was provided a trip update with no stops in it in the GTFS-RT update for 1559388516. The messages corresponding with this invalid trip were removed from the update during pre-processing.
  f"The trip with the ID {message_trip_id} was provided a trip update with "
/content/jupyter/gtfs-tripify/gtfs_tripify/ops.py:177: UserWarning: The trip with the ID 038900_E..S was provided a trip update with no stops in it in the GTFS-RT update for 1559388516. The messages corresponding with this invalid trip were removed from the update during pre-processing.
  f"The trip with the ID {message_trip_id} was provided a trip update with "
/content/jupyter/gtfs-tripify/gtfs_tripify/ops.py:177: UserWarning: The trip with the ID 028148_H..N was provided a trip update with no stops in it in the GTFS-RT update for 1559388516. The messages corresponding with this invalid trip were removed from the update durin

TypeError: tuple indices must be integers or slices, not dict

In [6]:
trains = pd.read_csv('logbook.csv')

FileNotFoundError: [Errno 2] File b'logbook.csv' does not exist: b'logbook.csv'

In [ ]:
trains.head()